# Bolt-on Governance API

This notebook outlines how to use the Bolt-on Governance API with [deployed LLM blueprints](https://docs.datarobot.com/en/docs/gen-ai/deploy-llm.html). LLM blueprints deployed from the playground implement the [`chat()` hook](https://docs.datarobot.com/en/docs/mlops/deployment/custom-models/custom-model-assembly/structured-custom-models.html#chat) in the custom model's `custom.py` file by default.

## Use the Bolt-on Governance API

You can use [the official Python library for the OpenAI API](https://github.com/openai/openai-python) to make chat completion requests to DataRobot LLM blueprint deployments:

In [ ]:
!pip install openai=="1.51.2"

In [ ]:
from openai import OpenAI

Specify the ID of the LLM blueprint deployment and your DataRobot API token:

In [ ]:
DEPLOYMENT_ID = "<SPECIFY_DEPLOYMENT_ID_HERE>"
DATAROBOT_API_TOKEN = "<SPECIFY_TOKEN_HERE>"

DEPLOYMENT_URL = f"https://app.datarobot.com/api/v2/deployments/{DEPLOYMENT_ID}"

Use the code below to create an OpenAI client:

In [ ]:
client = OpenAI(base_url=DEPLOYMENT_URL, api_key=DATAROBOT_API_TOKEN)

Use the code below to request a chat completion. See the [considerations](#considerations) below for more information on specifying the `model` parameter.

Note that specifying the system message in the request overrides the system prompt set in the LLM blueprint. Specifying other settings in the request, such as `max_completion_tokens`, overrides the settings of the LLM blueprint. 

In [ ]:
completion = client.chat.completions.create(
    model="datarobot-deployed-llm",
    messages=[
        {"role": "system", "content": "Answer with just a number."},
        {"role": "user", "content": "What is 2+3?"},
        {"role": "assistant", "content": "5"},
        {"role": "user", "content": "Now multiply the result by 4."},
        {"role": "assistant", "content": "20"},
        {"role": "user", "content": "Now divide the result by 2."},
    ],
)

In [ ]:
print(completion)

Use the following cell to request a chat completion with a streaming response.

In [ ]:
streaming_response = client.chat.completions.create(
    model="datarobot-deployed-llm",
    messages=[
        {"role": "system", "content": "Explain your thoughts using at least 100 words."},
        {"role": "user", "content": "What would it take to colonize Mars?"},
    ],
    stream=True,
)

In [ ]:
for chunk in streaming_response:
    content = chunk.choices[0].delta.content
    if content is not None:
        print(content, end="")

## Considerations

When using the Bolt-on Governance API, consider the following:

* If you implement the chat completion hook without modification, the `chat()` hook behaves differently than the `score()` hook. Specifically, the unmodified `chat()` hook [passes in the `model` parameter through the `completion_create_params` argument](https://docs.datarobot.com/en/docs/mlops/deployment/custom-models/custom-model-assembly/structured-custom-models.html#chat) while the `score()` hook specifies the model in the custom model code.
* If you [add a deployed LLM to the playground](https://docs.datarobot.com/en/docs/gen-ai/playground-tools/build-llm-blueprints.html#add-a-deployed-llm), the validation uses the value entered into the "Chat model ID" field as the `model` parameter value. Ensure the LLM deployment accepts this value as the `model` parameter. Alternatively, you can modify the implementation of the `chat()` hook to override the value of the `model` parameter, defining the intended model (for example, using a [runtime parameter](https://docs.datarobot.com/en/docs/mlops/deployment/custom-models/custom-model-assembly/custom-model-runtime-parameters.html)). For more information, see [GenAI troubleshooting](https://docs.datarobot.com/en/docs/gen-ai/genai-troubleshooting.html#custom-model-errors).
* The Bolt-on Governance API is also available in [GPU environments](https://docs.datarobot.com/en/docs/workbench/nxt-registry/nxt-model-workshop/nxt-open-source-textgen-template.html) for custom models running on `datarobot-drum>=1.14.3`.